In [1]:
%load_ext autoreload
%autoreload 2
# wd = '/mnt/openfact/users/msawinski/factue-task2'
wd = '/Users/marcinsawinski/Documents/GitHub/factue-task2'
import sys, os
os.chdir(wd)

In [ ]:
import pandas as pd
from pathlib import Path
import os
import numpy as np
root = Path("data/llm_output/persuasion/explain")
# Example path template
files = root.rglob("**/*.parquet")

# Read all files and add file path as a column
df_list = []
for f in files:
    df_part = pd.read_parquet(f)
    df_part['source_file'] = f  # add the file path
    df_list.append(df_part)

# Combine into one DataFrame
df = pd.concat(df_list, ignore_index=True)
df['split'] = df.source_file.astype(str).str.split('/',expand=True)[7]
df['partno'] = df.source_file.astype(str).str.split('/',expand=True)[9].str.split('_',expand=True)[1].str.split('.',expand=True)[0].astype(int)

In [ ]:
df

In [ ]:
defs = df[['prompt_name','updated_definition']].rename(columns={"updated_definition":"definition_update","prompt_name":"technique_id"})

In [ ]:
# Define the unwanted values
unwanted_values = [[None], ['']]

# Filter rows that do not contain any unwanted values
mask = defs.applymap(lambda x: x not in unwanted_values).all(axis=1)
filtered_df = defs[mask]
filtered_df = filtered_df.copy()
filtered_df['definition_update'] = filtered_df['definition_update'].apply(lambda x: x[0] if isinstance(x, np.ndarray) and x else None)
filtered_df = filtered_df.drop_duplicates(keep='first')
filtered_df

In [ ]:
from factue.methods.llm_calls import load_template_list
original_definitions = {}
prompts = load_template_list(job='persuasion', step="detect", prompt_version='v001')
for x in prompts.keys():
    original_definitions.update({x:prompts[x]['technique_desc']})


In [ ]:
filtered_df['definition_initial'] = filtered_df['technique_id'].map(original_definitions)

In [ ]:
disp(filtered_df, limit=10)

In [ ]:
import os

# Create an output directory if it doesn't exist
output_dir = "data/definitions/persuasion"
os.makedirs(output_dir, exist_ok=True)

# Group by 'prompt_name' and save each group to a separate Parquet file
for prompt, group_df in filtered_df.groupby('technique_id'):
    # Sanitize the filename (remove or replace problematic characters)
    file_path = os.path.join(output_dir, f"{prompt}.parquet")
    
    group_df.to_parquet(file_path, index=False)

In [ ]:
filtered_df.technique_id.value_counts()

# updated definitions

In [10]:
import pandas as pd
from pathlib import Path
import os
import numpy as np
from factue.utils.viz import disp
root = Path("data/llm_output/persuasion/define")
# Example path template
files = root.rglob("**/*.parquet")

# Read all files and add file path as a column
df_list = []
for f in files:
    df_part = pd.read_parquet(f)
    df_part['source_file'] = f  # add the file path
    df_list.append(df_part)

# Combine into one DataFrame
df = pd.concat(df_list, ignore_index=True)
df['split'] = df.source_file.astype(str).str.split('/',expand=True)[7]


In [11]:
new_defs = df[['technique_id','definition_initial','raw']].drop_duplicates(subset="technique_id", keep='last').reset_index(drop=True)
# new_defs['definition_base'] = new_defs['definition_base'].apply(lambda x: x[0] if isinstance(x, (list, np.ndarray)) and len(x) > 0 else x)
new_defs['raw'] = new_defs['raw'].apply(lambda x: x[0] if isinstance(x, (list, np.ndarray)) and len(x) > 0 else x)
disp(new_defs)

In [12]:
new_defs_dict = dict(zip(new_defs['technique_id'], new_defs['raw']))

In [13]:
from ruamel.yaml import YAML


yaml = YAML()
yaml.preserve_quotes = True

input_path =  "prompts/persuasion/detect/v001/prompt_content.yaml"
output_path = "prompts/persuasion/detect/v002/prompt_content.yaml"  # Overwrite or use a new file

with open(input_path, "r") as f:
    data = yaml.load(f)

for key in data:
    if key in new_defs_dict and isinstance(data[key], dict):
        data[key]['technique_desc'] = new_defs_dict[key]

with open(output_path, "w") as f:
    yaml.dump(data, f)

In [14]:
disp(df[['technique_id','definition_initial', 'definition_base','raw']])